In [1]:
import numpy as np
import pandas as pd

import warnings
warnings.filterwarnings("ignore")

In [2]:
from google.colab import files
files.upload()  # This will prompt you to upload the kaggle.json file


Saving kaggle.json to kaggle.json


{'kaggle.json': b'{"username":"poonambiswas","key":"f5121aaefca756f9315b5ff5d2a02cb0"}'}

In [3]:
!mkdir -p ~/.kaggle
!cp kaggle.json ~/.kaggle/
!chmod 600 ~/.kaggle/kaggle.json

In [4]:
!pip install kaggle

In [5]:
# Now you can use the Kaggle API to search for datasets
!kaggle datasets list -s 'gtfs delhi'


ref                                  title                    size  lastUpdated          downloadCount  voteCount  usabilityRating  
-----------------------------------  -----------------------  ----  -------------------  -------------  ---------  ---------------  
prasannadsa/delhi-open-transit-data  Delhi Open Transit Data  69MB  2023-10-06 13:36:23             55          1  0.7058824        
joyee19/delhi-bus-data               Delhi Bus Data           21MB  2022-02-04 18:41:04             35          4  0.1764706        


In [6]:
address = 'joyee19/delhi-bus-data'

In [7]:
# Replace 'username/dataset-name' with the actual dataset path on Kaggle
dataset_name = address  # Example: 'x/gtfs'

# Download and unzip the dataset
!kaggle datasets download -d {dataset_name} --unzip -p /content

# Verify files
!ls /content

Dataset URL: https://www.kaggle.com/datasets/joyee19/delhi-bus-data
License(s): unknown
 24% 5.00M/20.6M [00:00<00:00, 25.4MB/s]
100% 20.6M/20.6M [00:00<00:00, 75.4MB/s]
drive  GTFS  kaggle.json  sample_data


In [9]:
# List the files to verify the dataset is downloaded
!ls /content

drive  GTFS  kaggle.json  sample_data


In [10]:
import pandas as pd

# Load GTFS files into DataFrames
agency_df = pd.read_csv('/content/GTFS/agency.csv')

In [11]:
calendar_df = pd.read_csv('/content/GTFS/calendar.csv')
fare_attributes_df = pd.read_csv('/content/GTFS/fare_attributes.csv')
fare_rules_df = pd.read_csv('/content/GTFS/fare_rules.csv')
routes_df = pd.read_csv('/content/GTFS/routes.csv')
stop_times_df = pd.read_csv('/content/GTFS/stop_times.csv')
stops_df = pd.read_csv('/content/GTFS/stops.csv')
trips_df = pd.read_csv('/content/GTFS/trips.csv')

In [12]:
print("Agency Data:")
print(agency_df.head())
print("\nCalendar Data:")
print(calendar_df.head())
print("\nFare Attributes Data:")
print(fare_attributes_df.head())
print("\nFare Rules Data:")
print(fare_rules_df.head())
print("\nRoutes Data:")
print(routes_df.head())
print("\nStop Times Data:")
print(stop_times_df.head())
print("\nStops Data:")
print(stops_df.head())
print("\nTrips Data:")
print(trips_df.head())

Agency Data:
  agency_id                                       agency_name  \
0     DIMTS  Delhi Integrated Multi-Modal Transit System Ltd.   

              agency_url agency_timezone agency_lang  agency_phone  \
0  https://www.dimts.in/    Asia/Kolkata          en    1143090100   

   agency_fare_url  
0              NaN  

Calendar Data:
   start_date  end_date  monday  tuesday  wednesday  thursday  friday  \
0    20210901  20221001       1        1          1         1       1   

   saturday  sunday  service_id  
0         1       1           1  

Fare Attributes Data:
               fare_id  price currency_type  payment_method  transfers  \
0  DIMTS_706_3351_3352    5.0           INR               0          0   
1  DIMTS_706_3351_3353    5.0           INR               0          0   
2  DIMTS_706_3351_3354    5.0           INR               0          0   
3  DIMTS_706_3351_3355    5.0           INR               0          0   
4  DIMTS_706_3351_3356   10.0           INR      

In [13]:
stops_df.isnull().sum()

stop_id      0
stop_code    1
stop_name    0
stop_lat     0
stop_lon     0
zone_id      0
dtype: int64

In [14]:
stops_df = stops_df.dropna()

In [15]:
latitude, longitude = stops_df['stop_lat'].median(), stops_df['stop_lon'].median()

In [16]:
import folium

In [21]:
map1 = folium.Map(location=[latitude, longitude], zoom_start=11)

for lat, long, label,code in zip(stops_df['stop_lat'], stops_df['stop_lon'], stops_df['stop_name'],stops_df['stop_id']):
    folium.CircleMarker(
        [lat,long],
        radius = 1,
        color = 'Green',
        popup = (label,code),
        fill=True,
        fill_color='Red',
        fill_opacity=0.5
    ).add_to(map1)
map1

In [22]:
import spacy

# Load SpaCy model
nlp = spacy.load("en_core_web_sm")

def extract_keywords(query):
    doc = nlp(query)
    keywords = [token.text.lower() for token in doc if token.ent_type_ in {'GPE', 'LOC', 'FAC'} or token.pos_ in {'NOUN', 'PROPN'}]
    return keywords

def find_bus_station(query):
    keywords = extract_keywords(query)
    matches = stops_df[stops_df['stop_name'].str.lower().apply(lambda x: any(keyword in x.lower() for keyword in keywords))]
    if not matches.empty:
        return matches.to_dict(orient='records')
    return "Sorry, I couldn't find the bus station you're looking for."

# Test the system with user queries
queries = [
    "Where is Sarai Kale Khan?",
    "Tell me about Anand Vihar",
    "I want to know about ISBT Kashmere Gate"
]

for query in queries:
    result = find_bus_station(query)
    print(f"Query: {query}\nAnswer: {result}\n")


Query: Where is Sarai Kale Khan?
Answer: [{'stop_id': 30, 'stop_code': 'U01698', 'stop_name': 'Sarai Pipal Thala', 'stop_lat': 28.7206, 'stop_lon': 77.1671, 'zone_id': 30}, {'stop_id': 115, 'stop_code': 'U03346', 'stop_name': 'Jharkhandi', 'stop_lat': 28.66785, 'stop_lon': 77.28225, 'zone_id': 115}, {'stop_id': 242, 'stop_code': 'U01699', 'stop_name': 'Sarai Peepal Thala', 'stop_lat': 28.720417, 'stop_lon': 77.166983, 'zone_id': 242}, {'stop_id': 448, 'stop_code': 'U03147', 'stop_name': 'ISBT Sarai Kale Khan', 'stop_lat': 28.5911, 'stop_lon': 77.258083, 'zone_id': 448}, {'stop_id': 476, 'stop_code': 'U99679Z', 'stop_name': 'Tehkhand Depot DTC', 'stop_lat': 28.510917, 'stop_lon': 77.28116700000002, 'zone_id': 476}, {'stop_id': 571, 'stop_code': 'DC4454', 'stop_name': 'Purani Basti Rewla Khanpur', 'stop_lat': 28.56958400000001, 'stop_lon': 76.977685, 'zone_id': 571}, {'stop_id': 572, 'stop_code': 'DC5259', 'stop_name': 'Rewla Khanpur Depot', 'stop_lat': 28.568611, 'stop_lon': 76.97664, '